In [3]:
import numpy as np
import pandas as pd
import plotly.express as px

from tqdm import tqdm

In [4]:
np.random.seed(509)

# GDP

## Linear Regression

In [5]:
CORR_AMOUNT = 0
N_SAMPLES = 500

In [6]:

theta_optimal_lin_reg = np.arange(-5, 5+1, 1).reshape(-1, 1)


N_FEATURES = len(theta_optimal_lin_reg)

print(theta_optimal_lin_reg.shape, N_FEATURES)

(11, 1) 11


In [7]:
def get_tuplet_structure(param, dim):
    matrix = []
    for i in range(dim[0]):
        row = []
        for j in range(dim[1]):
            row.append(param**(abs(i-j)))
        matrix.append(row)
    return np.array(matrix)
    

In [8]:
cov_matrix = get_tuplet_structure(CORR_AMOUNT, [N_FEATURES, N_FEATURES])
cov_matrix

array([[1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
       [0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0],
       [0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0],
       [0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1]])

In [9]:
X_lin_reg = np.random.multivariate_normal(mean=np.zeros(N_FEATURES), cov=cov_matrix, size=N_SAMPLES) #for _ in range(N_SAMPLES)
X_lin_reg.shape

(500, 11)

In [10]:
y_lin_reg = X_lin_reg @ theta_optimal_lin_reg + np.random.randn(N_SAMPLES).reshape(-1,1)

In [11]:
np.mean(y_lin_reg)

-0.5644249105603445

In [12]:
def l2_loss(y_true, y_pred):
    loss = (y_true - y_pred).T @ (y_true - y_pred)
    return loss[0][0]

def erm_loss(theta, X, y):
    y_pred = X @ theta
    
    return l2_loss(y, y_pred) / len(y_pred)

In [13]:
def normal_equation(X, y):
    return np.linalg.solve(X.T @ X, X.T @ y)

In [14]:
erm_loss(theta_optimal_lin_reg, X_lin_reg, y_lin_reg)

0.9363976737531302

In [15]:
theta_analytic = normal_equation(X_lin_reg, y_lin_reg)

bayes_risk_analytic = erm_loss(theta_analytic, X_lin_reg, y_lin_reg)
print(bayes_risk_analytic)

0.9243536678257196


In [ ]:
beta = 1e-6

def gd(X, y, theta_prev, momentum_phi=0, step_size_initial=0.001, decay=0, num_steps=10_000,
       max_diff_theta=0.001, min_loss_improv=0.001, use_adagrad=False, use_rmsprop=False,
       rmspop_rho=0.9, use_adam=False, adam_rho1=0.9, adam_rho2=0.999, adam_bias_corr=True):
    if use_adagrad and use_rmsprop:
            raise ValueError(f"rmsprop and adagrad can't be True simultaneously")
        
    res = [{"iteration": 0,
            "theta": theta_prev,
            "loss": erm_loss(theta_prev, X, y)}]
    
    loss_prev = np.inf
    grad_step_prev = np.zeros(theta_analytic.shape)
    assert grad_step_prev.shape == theta_prev.shape
    
    # r (2nd moment)
    grad_accum = 0 
    last_grad = 0
    
    # s (1st moment)
    first_mom_accum = 0
    last_first_mom = 0
    
    
    for i in tqdm(range(num_steps)):
        if decay:
            step_size = step_size_initial * decay**(i / num_steps)
        else:
            step_size = step_size_initial # todo improve this
        
        gradient_transp = theta_prev.T @ X.T @ X - y.T @ X 
        # Todo This is ugly, fix this
        gradient = gradient_transp.T / N_SAMPLES
    
        assert gradient.shape == (X.shape[1], 1), \
            f"theta: {theta_prev.shape} | X: {X.shape} | y: {y.shape}"

        grad_step = momentum_phi * grad_step_prev - step_size * gradient

        if use_adagrad:
            grad_accum += grad_step * grad_step
        elif use_rmsprop:
            grad_accum += last_grad * adam_rho1 + grad_step * (1 - adam_rho1)
        elif use_adam:
            first_mom_accum += last_first_mom * adam_rho1 + grad_step * (1 - adam_rho1)
            grad_accum += last_grad * adam_rho2 + (grad_step * grad_step) * (1 - adam_rho2)

        
        if use_adam:
            if adam_bias_corr:
                first_mom_accum /= (1 - adam_rho1**(i+1))
                grad_accum /= (1- adam_rho2**(i+1))
        
        if use_adagrad or use_rmsprop:
            grad_step = grad_step / (beta + np.sqrt(grad_accum))  
        if use_adam:
            grad_step = grad_step * first_mom_accum / (beta + np.sqrt(grad_accum))  

        theta_new = theta_prev + grad_step
            
        
        res_dict = {"iteration": i+1,
                    "theta": theta_new,
                    "loss": erm_loss(theta_new, X, y)}

        res.append(res_dict)

        diff_thetas = theta_new - theta_prev 
        
        if max_diff_theta:
            if diff_thetas.T @ diff_thetas < max_diff_theta:
                print(f"Terminating after {i+1} iterations (theta stopped changing)")
                break
        if min_loss_improv:
            if np.abs(loss_prev - res_dict["loss"]) < min_loss_improv:
                print(f"Terminating after {i+1} iters (loss stopped improving)")
                break
            
        # print(f'{i} : {gradient[:2]} {gradient_prev[:2]}')
        # Update last values
        theta_prev = res_dict["theta"]        
        loss_prev = res_dict["loss"]
        grad_step_prev = grad_step
        last_grad = grad_accum
        last_first_mom = first_mom_accum
        



    res = pd.DataFrame(res)
    
    fig_loss = px.line(res, "iteration", "loss", title=f"Initial step size: {step_size_initial} | Momentum: {momentum_phi} | Decay {decay}")
    fig_loss.add_hline(y=bayes_risk_analytic, line_dash="dot", line_color="red", annotation_text="Bayes Risk Analytic")
    
    for i in range(len(theta_analytic)):
        res[f"theta{i}"] = res[f"theta"].apply(lambda x: x[i][0])
    
    fig_coefs = px.line(res, x="iteration", y=[f"theta{i}" for i in range(len(theta_analytic))])
    # add horizontal line for theta_optimal
    for i in range(len(theta_analytic)):
        fig_coefs.add_hline(y=theta_analytic[i][0], line_dash="dot", annotation_text=f"theta{i}")

    return res, fig_loss, fig_coefs
     

In [74]:
theta_start = np.zeros((N_FEATURES, 1))

# print("Dims")
# print(f"theta: {theta_start.shape} | X: {X_lin_reg.shape}| y: {y_lin_reg.shape}")
STEP_SIZE = 1e-3
MOMENTUM_PHI = 0.8
NUM_STEPS = 10_000

res = gd(X_lin_reg, y_lin_reg, theta_start, 
         step_size_initial=STEP_SIZE, 
         num_steps=NUM_STEPS,
         momentum_phi=0,
         max_diff_theta=0,
         min_loss_improv=0)

res_momentum = gd(X_lin_reg, y_lin_reg, theta_start, 
         step_size_initial=STEP_SIZE, 
         num_steps=NUM_STEPS,
         momentum_phi=0.8,
         max_diff_theta=0,
         min_loss_improv=0)

res_decay = gd(X_lin_reg, y_lin_reg, theta_start, 
         step_size_initial=STEP_SIZE, 
         num_steps=NUM_STEPS,
         momentum_phi=0,
         max_diff_theta=0,
         decay = 0.1,
         min_loss_improv=0)

res_momentum_decay = gd(X_lin_reg, y_lin_reg, theta_start, 
         step_size_initial=STEP_SIZE, 
         num_steps=NUM_STEPS,
         momentum_phi=0.8,
         decay=0.1,
         max_diff_theta=0,
         min_loss_improv=0)

res_adagrad = gd(X_lin_reg, y_lin_reg, theta_start, 
         step_size_initial=STEP_SIZE, 
         num_steps=NUM_STEPS,
         momentum_phi=0,
         decay=0,
         max_diff_theta=0,
         min_loss_improv=0, 
         use_adagrad=True)

res_rmsprop = gd(X_lin_reg, y_lin_reg, theta_start, 
         step_size_initial=STEP_SIZE, 
         num_steps=NUM_STEPS,
         momentum_phi=0,
         decay=0,
         max_diff_theta=0,
         min_loss_improv=0, 
         use_rmsprop=True)

res_adam_no_corr = gd(X_lin_reg, y_lin_reg, theta_start, 
         step_size_initial=STEP_SIZE, 
         num_steps=NUM_STEPS,
         momentum_phi=0,
         decay=0,
         max_diff_theta=0,
         min_loss_improv=0, 
         use_adam=True,
         adam_bias_corr=False)

res_adam_with_corr = gd(X_lin_reg, y_lin_reg, theta_start, 
         step_size_initial=STEP_SIZE, 
         num_steps=NUM_STEPS,
         momentum_phi=0,
         decay=0,
         max_diff_theta=0,
         min_loss_improv=0, 
         use_adam=True)



# Add Nesterov

  0%|          | 0/10000 [00:00<?, ?it/s]C:\Users\hayk_\AppData\Local\Temp\ipykernel_14940\303930646.py:56: RuntimeWarning:

invalid value encountered in sqrt

  0%|          | 0/10000 [00:00<?, ?it/s]C:\Users\hayk_\AppData\Local\Temp\ipykernel_14940\303930646.py:47: RuntimeWarning:

overflow encountered in add

C:\Users\hayk_\AppData\Local\Temp\ipykernel_14940\303930646.py:46: RuntimeWarning:

overflow encountered in add

  0%|          | 0/10000 [00:00<?, ?it/s]C:\Users\hayk_\AppData\Local\Temp\ipykernel_14940\303930646.py:47: RuntimeWarning:

overflow encountered in add

C:\Users\hayk_\AppData\Local\Temp\ipykernel_14940\303930646.py:53: RuntimeWarning:

overflow encountered in divide

C:\Users\hayk_\AppData\Local\Temp\ipykernel_14940\303930646.py:46: RuntimeWarning:

overflow encountered in add

100%|██████████| 10000/10000 [00:00<00:00, 16575.37it/s]


In [75]:
name_to_df = {
            'GD': res[0],
            'GD Momentum': res_momentum[0],
            'GD Decay': res_decay[0],
            'GD Momentum Decay': res_momentum_decay[0],
            "GD AdaGrad": res_adagrad[0],
            "GD RMSProp": res_rmsprop[0],
            "GD Adam no corr": res_adam_no_corr[0],
            "GD Adam corr": res_adam_with_corr[0]
            }

fig_loss = px.line(title="Loss over iterations")

for name, df in name_to_df.items():
    fig_loss.add_scatter(x=df["iteration"], y=df["loss"], mode="lines", name=name)
            
fig_loss.show()

In [53]:
theta_df = res_adagrad[0]

for i in range(len(theta_analytic)):
    theta_df[f"theta{i}"] = theta_df[f"theta"].apply(lambda x: x[i][0])
    

In [54]:
fig = px.line(theta_df, x="iteration", y=[f"theta{i}" for i in range(len(theta_analytic))])
# add horizontal line for theta_optimal
for i in range(len(theta_analytic)):
    fig.add_hline(y=theta_analytic[i][0], line_dash="dot", annotation_text=f"theta{i}")

fig.show()

# Kappa number

In [318]:
res = []
for i in np.linspace(0, .8, 100):
    cov_matrix_0 = get_tuplet_structure(i, dim=[N_FEATURES, N_FEATURES])

    hessian = cov_matrix_0.T @ cov_matrix_0

    eigenvals = np.linalg.eig(hessian).eigenvalues
    kappa = max(eigenvals) / min(eigenvals)
    
    res.append({"param": i, 
                "kappa": kappa})

df_kappa = pd.DataFrame(res)

px.line(df_kappa, "param", "kappa")

## 2 d Datasets

In [319]:
theta_optimal_2d = np.array((-3, 2)).reshape(-1,1)
x1 = np.random.uniform(-5, 5, 1_000).reshape(-1,1)
x2 = np.random.uniform(-5, 5, 1_000).reshape(-1,1)
X_2d = np.hstack([x1, x2])
print(X_2d.shape, theta_optimal_2d.shape)


y_2d = X_2d @ theta_optimal_2d

(1000, 2) (2, 1)


In [323]:
theta_init = np.zeros((X_2d.shape[1],1))

res_2d = gd(X_2d, y_2d, theta_init, step_size=0.00001)
px.line(res_2d, "iteration", "loss")

  0%|          | 26/10000 [00:00<00:00, 22070.82it/s]

Terminating after 27 iterations


In [328]:
res_2d["theta1"] = res_2d.theta.apply(lambda x: x[0][0])
res_2d["theta2"] = res_2d.theta.apply(lambda x: x[1][0])



In [330]:
fig = px.line(res_2d, x="iteration", y=["theta1", "theta2"])

# add horizontal line for theta_optimal
fig.add_hline(y=theta_optimal_2d[0][0], line_dash="dot", annotation_text="theta1")
fig.add_hline(y=theta_optimal_2d[1][0], line_dash="dot", annotation_text="theta2")

In [333]:
px.scatter_3d(res_2d, x="theta1", y="theta2", z="loss")

In [342]:
fig = px.density_heatmap(res_2d, x="theta1", y="theta2", z="loss")

bin_config = dict(
        start=res_2d.theta1.min(),
        end=res_2d.theta1.max(),
        size=11
    )

fig.update_traces(xbins=bin_config, ybins=bin_config)

In [609]:
import numpy as np
import plotly.graph_objects as go

# Define the function u(x, t) with a finite number of terms K
def u(x, t, K):
    sum_terms = 0
    for k in range(1, K + 1):
        term1 = (8 / (np.pi**3 * (2 * k - 1)**3)) * np.cos(np.pi * (2 * k - 1) * t)
        term2 = (4 / (np.pi**2 * (2 * k - 1)**2)) * np.sin(np.pi * (2 * k - 1) * t)
        term3 = np.sin(np.pi * (2 * k - 1) * x)
        sum_terms += (term1 + term2) * term3
    return sum_terms

# Create a grid of x and t values
x_vals = np.linspace(0, 1, 100)
t_vals = np.linspace(0, 1, 100)
X, T = np.meshgrid(x_vals, t_vals)

# Compute u(x, t) for the grid
K = 10  # Number of terms in the series
U = np.vectorize(lambda x, t: u(x, t, K))(X, T)

# Create a 3D surface plot
fig = go.Figure(data=[go.Surface(z=U, x=X, y=T, colorscale='Viridis')])

# Update layout
fig.update_layout(
    title="Visualization of u(x, t)",
    scene=dict(
        xaxis_title="x",
        yaxis_title="t",
        zaxis_title="u(x, t)"
    )
)

# Show the plot
fig.show()
